<a href="https://colab.research.google.com/github/fireHedgehog/music-intrument-OvA-model/blob/main/NSynth_overlay_instruments.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import tensorflow as tf
import numpy as np
import librosa
import os
from tensorflow.keras.models import load_model
import tensorflow_datasets as tfds


# Assuming 'label_map' and 'audio_to_spectrogram' function are defined as in Part One
def audio_to_spectrogram(audio_sample, sr=16000, n_fft=2048, hop_length=512):
    """Convert audio to spectrogram."""
    spectrogram = librosa.stft(audio_sample, n_fft=n_fft, hop_length=hop_length)
    spectrogram_db = librosa.amplitude_to_db(abs(spectrogram))
    return spectrogram_db

label_map = {
    0: 'bass',
    1: 'brass',
    2: 'flute',
    3: 'guitar',
    4: 'keyboard',
    5: 'mallet',
    6: 'organ',
    7: 'reed',
    8: 'string',
    9: 'synth_lead',
    10: 'vocal',
}


# Step 2: Load models

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

# base_dir = '/content/drive/MyDrive/nsynth_result_feb_28/models/'
base_dir = '/content/drive/MyDrive/output/models/'

model_cache = {}

for instrument_index, instrument_name in label_map.items():
    model_path = os.path.join(base_dir, f'family_{instrument_name}_classifier.h5')
    if os.path.exists(model_path):
        model_cache[instrument_index] = load_model(model_path)
    else:
        print(f"Model for {instrument_name} not found.")

# Load the NSynth dataset
nsynth_train = tfds.load('nsynth/gansynth_subset', split='train', shuffle_files=True)
nsynth_valid = tfds.load('nsynth/gansynth_subset', split='valid', shuffle_files=True)
nsynth_test = tfds.load('nsynth/gansynth_subset', split='test', shuffle_files=True)



Mounted at /content/drive
Model for synth_lead not found.


Dl Completed...:   0%|          | 0/229 [00:00<?, ? file/s]

Dataset nsynth downloaded and prepared to /root/tensorflow_datasets/nsynth/gansynth_subset/2.3.3. Subsequent calls will reuse this data.


# Step 3: get samples

In [ ]:
# Function to extract 100 samples per instrument family, using training data if necessary
def extract_samples(datasets, target_per_family=500):
    # Adjust the dictionary initialization to exclude synth_lead (id 9) explicitly
    samples_per_family = {k: [] for k in range(11) if k != 9}  # Exclude synth_lead with id 9

    for ds in datasets:
        for example in ds:
            family_id = example['instrument']['family'].numpy()
            if family_id == 9:  # Continue to skip synth_lead
                continue
            if len(samples_per_family.get(family_id, [])) < target_per_family:
                samples_per_family[family_id].append(example)
            if all(len(samples) == target_per_family for samples in samples_per_family.values()):
                break
    return samples_per_family

# Combine datasets starting with valid and test to prioritize their use before dipping into train
nsynth_datasets_balanced = extract_samples([nsynth_valid, nsynth_test, nsynth_train])
# nsynth_datasets_balanced = extract_samples([nsynth_train, nsynth_test,  nsynth_valid])

# Step 4: Generate test data



In [ ]:
import numpy as np
import librosa

def generate_noise_sample(size, sr=16000, duration=4):
    """Generate a random noise sample."""
    noise = np.random.randn(int(sr * duration))
    return librosa.stft(noise)

def overlay_spectrograms(spectrograms):
    """Overlay spectrograms."""
    overlay = np.sum(spectrograms, axis=0) / len(spectrograms)
    return overlay

def get_random_spectrogram(samples_per_family, exclude=[]):
    """Get a random spectrogram, ensuring it's not from an excluded family."""
    valid_families = [f for f in samples_per_family.keys() if f not in exclude]
    family_id = np.random.choice(valid_families)
    sample = np.random.choice(samples_per_family[family_id])
    audio_sample = sample['audio'].numpy()
    spectrogram = librosa.stft(audio_sample)

    spectrogram = librosa.stft(audio_sample, n_fft=2048, hop_length=512)
    spectrogram_db = librosa.amplitude_to_db(abs(spectrogram))

    return spectrogram_db, family_id

test_samples = []
true_labels = []

# Generate "No Instrument" samples
for _ in range(100):
    noise_spectrogram = generate_noise_sample(size=(1024, 1024))
    test_samples.append(noise_spectrogram)
    true_labels.append([0] * 10)

# Adjust label generation for vocal index and exclude synth_lead
for group_size in range(1, 11):
    for _ in range(100):
        spectrograms = []
        family_ids = []
        while len(spectrograms) < group_size:
            spectrogram, family_id = get_random_spectrogram(nsynth_datasets_balanced, exclude=family_ids)
            spectrograms.append(spectrogram)
            # Adjust family_id for vocal to compensate for the exclusion of synth_lead
            adjusted_family_id = family_id if family_id < 9 else 9
            family_ids.append(adjusted_family_id)

        overlayed_spectrogram = overlay_spectrograms(spectrograms)
        # Initialize label with 0s, considering synth_lead exclusion
        label = [0] * 10
        for fid in family_ids:
            label[fid] = 1
        test_samples.append(overlayed_spectrogram)
        true_labels.append(label)

step 5, plot samples


In [ ]:
import matplotlib.pyplot as plt
import librosa.display
import numpy as np
import os
import textwrap

label_map_new = {
    0: 'bass',
    1: 'brass',
    2: 'flute',
    3: 'guitar',
    4: 'keyboard',
    5: 'mallet',
    6: 'organ',
    7: 'reed',
    8: 'string',
    9: 'vocal',
}


def plot_and_save_example_per_class(true_labels, test_samples, label_map, save_path):
    saved_classes = set()  # To track which classes have been saved

    for i, (labels, spectrogram) in enumerate(zip(true_labels, test_samples)):
        num_instruments = sum(labels)
        if num_instruments in saved_classes:
            continue  # Skip if already saved an example for this number of instruments

        saved_classes.add(num_instruments)  # Mark this number of instruments as saved

        # Prepare the spectrogram for plotting
        S_db = librosa.amplitude_to_db(np.abs(spectrogram))

        plt.figure(figsize=(10, 4))
        librosa.display.specshow(S_db, sr=16000, hop_length=512, y_axis='log', x_axis='time')

        # Instrument names for the title
        instrument_names = [label_map[idx] for idx, present in enumerate(labels) if present]
        title = ', '.join(instrument_names)

        # Use line breaks for long titles
        if len(title) > 50:
            title = '\n'.join(textwrap.wrap(title, 50))

        plt.title(title, fontsize=10)
        plt.colorbar(format='%+2.0f dB')
        plt.tight_layout()

        # Simplify filename based on the number of instruments
        if num_instruments == 0:
            file_name = "No_Instrument"
        elif num_instruments == 1:
            file_name = "Solo"
        else:
            file_name = f"{num_instruments}_Instruments"

        # Save the figure
        fig_save_path = os.path.join(save_path, f"{file_name}.png")
        plt.savefig(fig_save_path)
        plt.close()
        print(f"Figure saved as {fig_save_path}")

        # Break if examples for all classes have been saved
        if len(saved_classes) == 11:  # Account for 0 to 10 instruments
            break

# Define the save path
save_path = '/content/drive/MyDrive/EMR_output/figures/'
os.makedirs(save_path, exist_ok=True)

# Execute the function to plot and save examples
plot_and_save_example_per_class(true_labels, test_samples, label_map_new, save_path)
# print(true_labels)


Figure saved as /content/drive/MyDrive/EMR_output/figures/No_Instrument.png
Figure saved as /content/drive/MyDrive/EMR_output/figures/Solo.png
Figure saved as /content/drive/MyDrive/EMR_output/figures/2_Instruments.png
Figure saved as /content/drive/MyDrive/EMR_output/figures/3_Instruments.png
Figure saved as /content/drive/MyDrive/EMR_output/figures/4_Instruments.png
Figure saved as /content/drive/MyDrive/EMR_output/figures/5_Instruments.png
Figure saved as /content/drive/MyDrive/EMR_output/figures/6_Instruments.png
Figure saved as /content/drive/MyDrive/EMR_output/figures/7_Instruments.png
Figure saved as /content/drive/MyDrive/EMR_output/figures/8_Instruments.png
Figure saved as /content/drive/MyDrive/EMR_output/figures/9_Instruments.png
Figure saved as /content/drive/MyDrive/EMR_output/figures/10_Instruments.png


# Step 5: Evaluate the models on generated test data

In [ ]:
import os
import csv


def get_thre_from_hardcode_startpoint():
    """
          Highest bass accuracy: 0.5655, corresponding threshold: 0.0030
          Highest brass accuracy: 0.6673, corresponding threshold: 0.0007
          Highest flute accuracy: 0.5282, corresponding threshold: 0.1227
          Highest guitar accuracy: 0.5764, corresponding threshold: 0.0075
          Highest keyboard accuracy: 0.5764, corresponding threshold: 0.0001
          Highest mallet accuracy: 0.7300, corresponding threshold: 0.0001
          Highest organ accuracy: 0.5964, corresponding threshold: 0.0007
          Highest reed accuracy: 0.6873, corresponding threshold: 0.0018
          Highest string accuracy: 0.7218, corresponding threshold: 0.0927
          Highest vocal accuracy: 0.7564, corresponding threshold: 0.0056
    """
    base_thresholds = [
        0.0030, 0.0007, 0.1227, 0.0075, 0.0001, 0.0001, 0.0007, 0.0018, 0.0927, 0.0056
    ]
    random_adjustments = [
        np.random.uniform(-0.0001, 0.1) for i in range(10)
    ]
    # Adjust each base threshold by a random value within the specified range
    adjusted_thresholds = [max(0, base + adjustment) for base, adjustment in zip(base_thresholds, random_adjustments)]
    return adjusted_thresholds

def calculate_exact_match_ratio(true_labels, pred_labels):
    exact_matches = sum([1 for true, pred in zip(true_labels, pred_labels) if true == pred])
    return exact_matches / len(true_labels)

def optimize_threshold(test_samples, true_labels, model_cache, max_iterations=100):
    base_dir = '/content/drive/MyDrive/EMR_output/tests/'
    os.makedirs(base_dir, exist_ok=True)

    for i in range(max_iterations):
        # Generate a unique random threshold for each model
        # thresholds = [np.random.uniform(0.0001, 0.01) for _ in range(10)]
        thresholds = get_thre_from_hardcode_startpoint()
        # thresholds = [
        #     0.0030, 0.0007, 0.1227, 0.0075, 0.0001, 0.0001, 0.0007, 0.0018, 0.0927, 0.0056
        # ]
        pred_labels = predict_labels_with_threshold(test_samples, model_cache, thresholds)
        emr = calculate_exact_match_ratio(true_labels, pred_labels)
        save_results(i, true_labels, pred_labels, emr, thresholds, base_dir)

def predict_labels_with_threshold(test_samples, model_cache, thresholds):
    pred_labels = []
    for sample in test_samples:
        pred_array = [0] * 10  # Initialize prediction array for 10 instruments

        for index, model in model_cache.items():
            # Adjust index for vocal to account for the exclusion of synth_lead
            array_index = index if index < 9 else 9
            # Prepare sample for prediction
            sample_prepared = np.expand_dims(np.expand_dims(sample, axis=0), axis=-1)
            pred = model.predict(sample_prepared)[0]
            # Use the threshold specific to the current model
            pred_array[array_index] = 1 if pred > thresholds[array_index] else 0

        pred_labels.append(pred_array)
    return pred_labels

def save_results(index, true_labels, pred_labels, emr, thresholds, base_dir):
    # Constructing filename with thresholds
    thresholds_str = '-'.join([f"{i+1}:{thresh:.4f}" for i, thresh in enumerate(thresholds)])
    filename = f"{index}_emr[{emr:.4f}]_thresholds[{thresholds_str}].csv"
    save_path = os.path.join(base_dir, filename)

    with open(save_path, mode='w', newline='') as file:
        writer = csv.writer(file)
        writer.writerow(['True Labels', 'Pred Labels'])
        for t, p in zip(true_labels, pred_labels):
            true_label_str = ' '.join(map(str, t))
            pred_label_str = ' '.join(map(str, p))
            writer.writerow([true_label_str, pred_label_str])
    print(f"Results saved to: {save_path}")

# Call the optimization function
optimize_threshold(test_samples, true_labels, model_cache, 30)

"""
def predict_labels(test_samples, model_cache):
    pred_labels = []

    for sample in test_samples:
        pred_array = [0] * 10  # Initialize prediction array for 10 instruments

        for index, model in model_cache.items():
            # Prepare sample for prediction (add batch dimension and channel dimension)
            sample_prepared = np.expand_dims(np.expand_dims(sample, axis=0), axis=-1)

            # Predict using the modele
            pred = model.predict(sample_prepared)[0]
            print(pred)
            # print(pred)

            # Adjust index for vocal to account for the exclusion of synth_lead
            array_index = index if index < 9 else 9

            # adjut threshold to 0.3, 0.4 0.5 0.6
            pred_array[array_index] = 1 if pred > 0.2 else 0

        print(pred_array)
        pred_labels.append(pred_array)

    return pred_labels
"""

"""
# Predict labels using the trained models
pred_labels = predict_labels(test_samples, model_cache)

# Calculate the exact match ratio
exact_match_ratio = calculate_exact_match_ratio(true_labels, pred_labels)
print(f"Exact Match Ratio: {exact_match_ratio:.4f}")

# Assuming true_labels and pred_labels are already defined and populated
true_labels_array = np.array(true_labels)
pred_labels_array = np.array(pred_labels)

save_path = '/content/drive/MyDrive/EMR_output/tests/labels_comparison.csv'

# Ensure the directory exists
dir_name = os.path.dirname(save_path)
os.makedirs(dir_name, exist_ok=True)

# Save the true and predicted labels to a CSV file
with open(save_path, mode='w', newline='') as file:
    writer = csv.writer(file)
    # Write the header
    writer.writerow(['True Labels', 'Pred Labels'])
    # Write the true and predicted labels
    for t, p in zip(true_labels, pred_labels):
        true_label_str = ' '.join(map(str, t))
        pred_label_str = ' '.join(map(str, p))
        writer.writerow([true_label_str, pred_label_str])

print(f"True and predicted labels saved to: {save_path}")
"""


try optimization

In [ ]:
import os
import csv
import numpy as np
from sklearn.metrics import jaccard_score

def get_thre_from_hardcode_startpoint():
    base_thresholds = [
        0.0030, 0.0007, 0.1227, 0.0075, 0.0001, 0.0001, 0.0007, 0.0018, 0.0927, 0.0056
    ]
    random_adjustments = [np.random.uniform(-0.0001, 0.1) for _ in range(10)]
    adjusted_thresholds = [max(0, base + adjustment) for base, adjustment in zip(base_thresholds, random_adjustments)]
    return adjusted_thresholds

def calculate_exact_match_ratio(true_labels, pred_labels):
    exact_matches = sum(1 for true, pred in zip(true_labels, pred_labels) if true == pred)
    return exact_matches / len(true_labels)

def predict_labels_with_threshold(test_samples, model_cache, thresholds):
    pred_labels = []
    for sample in test_samples:
        pred_array = [0] * 10  # Assuming 10 labels
        # Assuming 10 labels for index, model in enumerate(model_cache):
        for index, model in model_cache.items():
            array_index = index if index < 9 else 9
            sample_prepared = np.expand_dims(np.expand_dims(sample, axis=0), axis=-1)
            pred = model.predict(sample_prepared)[0]  # Simulate model prediction
            pred_array[array_index] = 1 if pred > thresholds[array_index] else 0
        pred_labels.append(pred_array)
    return pred_labels

def save_results(index, true_labels, pred_labels, emr, thresholds, base_dir):
    thresholds_str = '-'.join([f"{i+1}:{thresh:.4f}" for i, thresh in enumerate(thresholds)])
    filename = f"{index}_emr[{emr:.4f}]_thresholds[{thresholds_str}].csv"
    save_path = os.path.join(base_dir, filename)
    with open(save_path, mode='w', newline='') as file:
        writer = csv.writer(file)
        writer.writerow(['True Labels', 'Pred Labels'])
        for t, p in zip(true_labels, pred_labels):
            writer.writerow([' '.join(map(str, t)), ' '.join(map(str, p))])
    print(f"Results saved to: {save_path}")

def optimize_threshold(test_samples, true_labels, model_cache, max_iterations=100):
    base_dir = 'EMR_output/tests/'
    os.makedirs(base_dir, exist_ok=True)
    for i in range(max_iterations):
        thresholds = get_thre_from_hardcode_startpoint()
        pred_labels = predict_labels_with_threshold(test_samples, model_cache, thresholds)
        emr = calculate_exact_match_ratio(true_labels, pred_labels)
        save_results(i, true_labels, pred_labels, emr, thresholds, base_dir)


def calculate_jaccard_similarity(true_labels, pred_labels):
    # Assuming true_labels and pred_labels are binary label indicators for multi-label classification
    # Calculate the average Jaccard similarity score across all labels
    jaccard_sim = jaccard_score(true_labels, pred_labels, average='samples')
    return jaccard_sim

def optimize_threshold_based_on_jaccard(test_samples, true_labels, model_cache, max_iterations=100):
    base_dir = 'EMR_output/tests/'
    os.makedirs(base_dir, exist_ok=True)

    best_jaccard = 0
    best_thresholds = None

    for i in range(max_iterations):
        thresholds = get_thre_from_hardcode_startpoint()
        pred_labels = predict_labels_with_threshold(test_samples, model_cache, thresholds)
        current_jaccard = calculate_jaccard_similarity(true_labels, pred_labels)

        if current_jaccard > best_jaccard:
            best_jaccard = current_jaccard
            best_thresholds = thresholds
            print(f"New best Jaccard similarity: {best_jaccard} at iteration {i}")
            save_results(i, true_labels, pred_labels, best_jaccard, thresholds, base_dir)

    print(f"Best Jaccard similarity: {best_jaccard} with thresholds: {best_thresholds}")


def optimize_individual_thresholds(test_samples, true_labels, model_cache, max_iterations=10, step=0.01):
    base_thresholds = get_thre_from_hardcode_startpoint()  # Start with your initial thresholds
    best_thresholds = base_thresholds[:]
    best_jaccard = calculate_jaccard_similarity(true_labels, predict_labels_with_threshold(test_samples, model_cache, best_thresholds))

    for _ in range(max_iterations):
        for index in range(len(best_thresholds)):
            temp_thresholds = best_thresholds[:]
            # Explore both directions: increasing and decreasing the threshold
            for direction in [-step, step]:
                temp_thresholds[index] += direction
                # Ensure thresholds are within valid range
                temp_thresholds[index] = max(0, min(temp_thresholds[index], 1))
                pred_labels = predict_labels_with_threshold(test_samples, model_cache, temp_thresholds)
                current_jaccard = calculate_jaccard_similarity(true_labels, pred_labels)

                if current_jaccard > best_jaccard:
                    best_jaccard = current_jaccard
                    best_thresholds = temp_thresholds[:]
                    print(f"Improved Jaccard to {best_jaccard} with thresholds at index {index}: {best_thresholds}")
                    # Optionally, break if an improvement is found, to move to the next index
                    break

    return best_thresholds


optimize_individual_thresholds(test_samples, true_labels, model_cache, max_iterations=10, step=0.01)

# Run the optimization function
# optimize_threshold(test_samples, true_labels, model_cache, 30)


AP optimization

In [ ]:
from sklearn.metrics import average_precision_score

# Assuming all prior setup and functions for data loading and preprocessing

def predict_label_probabilities(test_samples, model_cache):
    pred_probs = []
    for sample in test_samples:
        pred_prob_sample = np.zeros(10)  # Ensure this matches the number of models/labels
        for index, model in model_cache.items():
            array_index = index if index < 9 else 9  # Skip model 9, adjust model 10 to position 9
            sample_prepared = np.expand_dims(np.expand_dims(sample, axis=0), axis=-1)
            pred_prob_sample[array_index] = model.predict(sample_prepared)[0]
        pred_probs.append(pred_prob_sample)
    return np.array(pred_probs)

def calculate_average_precision_scores(true_labels, pred_probs):
    ap_scores = [average_precision_score(true_labels[:, i], pred_probs[:, i]) for i in range(true_labels.shape[1])]
    mean_ap = np.mean(ap_scores)
    return mean_ap, ap_scores

def save_results_with_probabilities(index, true_labels, pred_probs, ap_scores, mean_ap, base_dir):
    filename = f"{index}_mean-ap[{mean_ap:.4f}].csv"
    save_path = os.path.join(base_dir, filename)
    with open(save_path, mode='w', newline='') as file:
        writer = csv.writer(file)
        writer.writerow(['True Labels', 'Predicted Probabilities', 'AP Scores'])
        for t, p, ap in zip(true_labels, pred_probs, ap_scores):
            writer.writerow([' '.join(map(str, t)), ' '.join(map(str, p)), f"{ap:.4f}"])
    print(f"Results saved to: {save_path}")

def optimize_based_on_ap(test_samples, true_labels, model_cache, max_iterations=1):
    base_dir = 'EMR_output/tests/'
    os.makedirs(base_dir, exist_ok=True)
    best_ap = 0
    for i in range(max_iterations):
        pred_probs = predict_label_probabilities(test_samples, model_cache)
        mean_ap, ap_scores = calculate_average_precision_scores(np.array(true_labels), pred_probs)
        if mean_ap > best_ap:
            best_ap = mean_ap
            print(f"New best AP: {best_ap} at iteration {i}")
            save_results_with_probabilities(i, true_labels, pred_probs, ap_scores, mean_ap, base_dir)

# Example usage (assuming test_samples, true_labels, and model_cache are already defined)
optimize_based_on_ap(test_samples, true_labels, model_cache, 30)


1/1 [==============================] - 0s 26ms/step


<ipython-input-8-e864c7cbfde9>:12: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  pred_prob_sample[array_index] = model.predict(sample_prepared)[0]


Streaming output truncated to the last 5000 lines.
1/1 [==============================] - 0s 24ms/step
New best AP: 0.5467061311566345 at iteration 0
Results saved to: EMR_output/tests/0_mean-ap[0.5467].csv
1/1 [==============================] - 0s 25ms/step


<ipython-input-8-e864c7cbfde9>:12: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  pred_prob_sample[array_index] = model.predict(sample_prepared)[0]


Streaming output truncated to the last 5000 lines.
1/1 [==============================] - 0s 28ms/step


...

Streaming output truncated to the last 5000 lines.
1/1 [==============================] - 0s 26ms/step


<ipython-input-8-e864c7cbfde9>:12: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  pred_prob_sample[array_index] = model.predict(sample_prepared)[0]


Streaming output truncated to the last 5000 lines.
1/1 [==============================] - ETA: 0s

<ipython-input-8-e864c7cbfde9>:12: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  pred_prob_sample[array_index] = model.predict(sample_prepared)[0]


Streaming output truncated to the last 5000 lines.
1/1 [==============================] - ETA: 0s